In [9]:
import numpy as np 
import pandas as pd 
import math 

In [29]:
# sampling x 
x1 = np.random.normal(3 , 2, (1000000,) ) 
x2 = np.random.normal(-1, 2 , (1000000,)) 
x = np.zeros((1000000, 3)) 

x[:, 0] = 1 # adding intercept term 
x[:, 1] = x1 
x[:, 2] = x2 
# print(np.var(x[:, 1]))  

# sampling y 

theta = np.array([3,1,2]) 
y = np.matmul(x, theta) 
y += np.random.normal(0, math.sqrt(2) , y.shape)  
# print(np.mean(y)) 



In [92]:
def compute_batch_error(X, Y, theta, batch_size, batch_number):
    X_batch = X[batch_size  * (batch_number - 1)   : batch_size * (batch_number - 1) + batch_size, :] 
    Y_batch = Y[ batch_size  * (batch_number - 1)   : batch_size * (batch_number - 1) + batch_size] 

    Z = Y_batch - np.matmul(X_batch, theta)
    error = np.matmul(np.transpose(Z), Z) / (2 * batch_size) 
    return error  

In [97]:
def compute_batch_gradient(X, Y, theta, batch_size, batch_number):
    X_batch = X[batch_size  * (batch_number - 1)   : batch_size * (batch_number - 1) + batch_size, :] 
    Y_batch = Y[ batch_size  * (batch_number - 1)   : batch_size * (batch_number - 1) + batch_size] 
    Z_batch = Y_batch - np.matmul(X_batch, theta) 
    # print(Z)
    gradient = np.zeros(theta.size) 
    for j in range(theta.size):
        X_j = X_batch[:, j] 
        gradient[j] = np.sum(Z_batch * X_j)/ batch_size 
    return gradient

In [249]:
def minibatch_gradient_descent(X, Y, batch_size, k, gamma):
    current_batch_number = 1 
    theta = np.zeros(X[0].size) 
    print(theta) 
    initial_error = compute_batch_error(X, Y, theta,  batch_size, int(current_batch_number) ) 
    epsilon = 0.00001 * initial_error 

    # print(f"factor is {pow(batch_size, -0.5)}")
    #we decrease epsilon for large batch sizes, since smaller batch sizes converge more noisily to the 
    # optima, thus they require a larger epsilon 
     
    epsilon = pow(batch_size, -0.5) * epsilon 
    max_count = int(1/epsilon) 
    # to avoid oscillations, we introduce this cap  

    print(f"maxcount is {max_count}")

    learning_parameter = 0.001
    MOD = Y.size / batch_size 
    no_of_iterations = 0 


    error_arr = []
    running_avg = 0 
    previous_running_avg = 0 

    for i in range(k):
        grad = compute_batch_gradient(X, Y, theta, batch_size, int(current_batch_number) ) 
        theta = theta + learning_parameter * grad 
        curr_error = compute_batch_error(X, Y,theta,  batch_size, int(current_batch_number) )
        error_arr.append(curr_error) 
        running_avg += curr_error 
        current_batch_number = (current_batch_number + 1) 
        if (current_batch_number > MOD):  current_batch_number -= MOD 
        no_of_iterations += 1


    running_avg /= k
    last_count = 0  # no of consecutive times difference in averages is less than epsilon  
    # epsilon = 0.000001 * running_avg 
    
    while (last_count < gamma and no_of_iterations < max_count):
        
        
        previous_running_avg = running_avg 
        previous_error = error_arr.pop(0) 

        # print(f" batch size, batch num {batch_size} {current_batch_number}") 
        grad = compute_batch_gradient(X, Y, theta, batch_size, int(current_batch_number) ) 
        theta = theta + learning_parameter * grad 
        
        curr_error = compute_batch_error(X, Y,theta,  batch_size, int(current_batch_number) ) 
        error_arr.append(curr_error) 

        running_avg = running_avg + (curr_error - previous_error)/k  

        # print(f"current theta is {theta}") 
        # print(f"last count {last_count}")
        print(f"average error is {running_avg}") 
        
        if (abs(previous_running_avg - running_avg) < epsilon) :  last_count += 1 
        else: last_count = 0
        
        no_of_iterations += 1 
        current_batch_number = (current_batch_number + 1) 
        if (current_batch_number > MOD):  current_batch_number -= MOD 

    print(f"no of iterations is {no_of_iterations}") 
    print(f"learned theta is {theta}") 
    return theta 
    

In [146]:
def batch_gradient_descent(X, Y):
    theta = np.zeros(X[0].size) 
    print(theta) 
    initial_error = compute_batch_error(X, Y, theta,  Y.size , 1 ) 
    error = initial_error 
    epsilon = 0.0001 * initial_error 
    # print(f"intial error is {initial_error}")
    learning_parameter = 0.001
    no_of_iterations = 0 

    previous_error = 2*error 
    while ( previous_error - error > epsilon) : 

        previous_error = error 
        grad = compute_batch_gradient(X, Y, theta, Y.size, 1 ) 
        theta = theta + learning_parameter * grad 
        
        error = compute_batch_error(X, Y,theta,  Y.size , 1 ) 


        # print(f"current theta is {theta}") 

        no_of_iterations += 1 

    print(f"no of iterations is {no_of_iterations}") 
    print(f"learned theta is {theta}") 
    return theta 
    

In [270]:
batch_size = 1
k = 10
gamma = 1
minibatch_gradient_descent(x, y, batch_size, k, gamma) 


[0. 0. 0.]
maxcount is 2889463
average error is 16.247118666040553
average error is 16.625927673958394
average error is 15.477137896441949
average error is 18.8732831915729
average error is 25.555488970037914
average error is 23.372265986997938
average error is 19.536236644350925
average error is 19.68222833900979
average error is 21.232262239273282
average error is 21.207503285993116
average error is 18.401993237019322
average error is 18.549689346369224
average error is 17.4142594463915
average error is 15.847244145147195
average error is 8.450304932264505
average error is 9.125337136154181
average error is 10.646990675801256
average error is 11.310031767813523
average error is 11.934326442077037
average error is 11.7083642838737
average error is 11.82458905271622
average error is 11.427067848301004
average error is 11.380038544629803
average error is 9.942012320296936
average error is 9.025122087363881
average error is 9.109843726028188
average error is 7.707531900395612
average err

array([2.98313453, 1.05048981, 2.00002717])

In [234]:
batch_size = 1000000 
k = 1   
gamma = 1
minibatch_gradient_descent(x, y, batch_size, k, gamma) 


[0. 0. 0.]
maxcount is 5264529
average error is 18.42852622235206
average error is 18.15513851514319
average error is 17.8880953957338
average error is 17.62722438699031
average error is 17.372357950982533
average error is 17.123333345391995
average error is 16.87999248411218
average error is 16.64218180191821
average error is 16.40975212308719
average error is 16.18255853385342
average error is 15.96046025858678
average error is 15.743320539585191
average error is 15.531006520375593
average error is 15.323389132421024
average error is 15.120342985134094
average error is 14.921746259100326
average error is 14.727480602417494
average error is 14.537431030059942
average error is 14.3514858261795
average error is 14.169536449257068
average error is 13.991477440021711
average error is 13.817206332056283
average error is 13.646623565011117
average error is 13.479632400349544
average error is 13.316138839551298
average error is 13.15605154470195
average error is 12.999281761398635
average er

KeyboardInterrupt: 

In [265]:
batch_size = 100 
k = 10
gamma = 2
minibatch_gradient_descent(x, y, batch_size, k, gamma) 

[0. 0. 0.]
maxcount is 48487
average error is 16.894201092610214
average error is 17.070869247738027
average error is 17.25762982887739
average error is 16.636040444050977
average error is 16.5064640009206
average error is 16.24363780322035
average error is 16.3797382693983
average error is 15.759004715297914
average error is 15.25723535307058
average error is 14.927700102146295
average error is 14.789606104220796
average error is 14.659110562057531
average error is 14.578803066130188
average error is 14.744240663359678
average error is 14.80355180211168
average error is 14.43615714164186
average error is 13.961894614659872
average error is 13.749503990780457
average error is 14.111341926175818
average error is 13.889035949542757
average error is 13.772345169609753
average error is 13.39229988927509
average error is 13.082285928947353
average error is 12.930546585260588
average error is 12.320819437062148
average error is 11.97655854549202
average error is 11.952050238807885
average er

array([3.0032631 , 0.99897861, 1.99748982])

In [272]:
batch_size = 10000 
k = 5
gamma = 1

minibatch_gradient_descent(x, y, batch_size, k, gamma) 

[0. 0. 0.]
maxcount is 520283
average error is 17.76474528858157
average error is 17.48286696124476
average error is 17.280556628536953
average error is 17.03395609176234
average error is 16.802603911723768
average error is 16.735718825885748
average error is 16.462522443832807
average error is 16.245558163697257
average error is 16.027519350754886
average error is 15.76300245447949
average error is 15.448462529215254
average error is 15.307505132202863
average error is 15.079523971308076
average error is 14.854541509034725
average error is 14.784062978352665
average error is 14.62053788717546
average error is 14.42543968914924
average error is 14.247587537161698
average error is 14.061252781262162
average error is 13.82142118166906
average error is 13.678261888021654
average error is 13.510498740068742
average error is 13.360445341207084
average error is 13.138016076931201
average error is 12.947327220430367
average error is 12.787631884735625
average error is 12.648984007194827
avera

array([2.8486209 , 1.03271841, 1.98756523])

In [273]:
test_set = pd.read_csv("./ass1_data/data/q2/q2test.csv") 
test_set = test_set.to_numpy() 
print(test_set) 

[[ 16.678  13.018  45.537]
 [  6.583  -5.539  -1.17 ]
 [-19.837   6.089  -3.646]
 ...
 [  6.381   2.484  13.018]
 [  3.138  -5.425  -6.873]
 [  5.502  -8.332  -7.749]]
